In [1]:
import torch
import torch.nn as nn
torch.cuda.is_available()

True

In [2]:
from transformers import LlamaTokenizer, LlamaForCausalLM
from peft import get_peft_model, PeftConfig, PeftModel

loc = 'sqllama-out3'

config = PeftConfig.from_pretrained(loc)
print(config)


tokenizer = LlamaTokenizer.from_pretrained(
    "decapoda-research/llama-7b-hf")
   
tokenizer.pad_token_id = 0
tokenizer.padding_side = 'left'

model = LlamaForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
    torch_dtype=torch.float16
)

model = PeftModel.from_pretrained(
    model, loc,
    torch_dtype=torch.float16,
    device_map="auto"
    )

#model.push_to_hub('LlamaSQL-3')

#model = prepare_model_for_int8_training(model)

#model = get_peft_model(model,config)

/home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /opt/conda did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 113
CUDA SETUP: Loading binary /home/matt/hf/sqllama-V0/.venv/lib/python3.7/site-packages/bitsandbytes/libbitsandbytes_cuda113.so...
PeftConfig(peft_type='LORA', base_model_name_or_path='decapoda-research/llama-7b-hf', task_type='CASUAL_LM', inference_mode=True)


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [4]:
import random
import json

# defined by WikiSQL

agg_ops = ['', 'MAX', 'MIN', 'COUNT', 'SUM', 'AVG']
cond_ops = ['=', '>', '<', 'OP']
syms = ['SELECT', 'WHERE', 'AND', 'COL', 'TABLE', 'CAPTION', 'PAGE', 'SECTION', 'OP', 'COND', 'QUESTION', 'AGG', 'AGGOPS', 'CONDOPS']

def fix_repr(d,cols,types,tid):
    sel_index=d['sel'] 
    agg_index=d['agg']
    conditions=d['conds']
    col = cols[sel_index]
    rep = 'SELECT {agg} {sel} FROM {tid}'.format(
            agg=agg_ops[agg_index],
            sel=col,
            tid=tid
            )
    if conditions:
        cs = []
        for i, o, v in conditions:
            #print(i,cols)
            nm = cols[i]
            op = cond_ops[o]
            
            if types[i] in ['text']:
                val = f"\'{v}\'"
            else:
                val = v
            cs.append(f'{nm} {op} {val}')
        #print(cs)

        rep +=  ' WHERE ' + ' AND '.join(cs)
    
    return rep

tbl_cols = {}
tbl_types = {}
tbl_str = {}

prefix = 'Below is a question that describes a data request, paired with an input that describes a SQL table.  Write a SQL query that retrieves the data.'

def tbl_def_to_string(id, header, types):
    s = f'table: {id}\ncolumns: ' + ','.join(header)
    return s

with open('data/train.tables.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['id']
        hdr = js['header']
        ts = js['types']
        tbl_str[id] = tbl_def_to_string(id,hdr,ts)
        tbl_cols[id] = hdr
        tbl_types[id] = ts

q_s = []
a_s = []

with open('data/train.jsonl') as f:
    for line in f:
        js = json.loads(line)
        id = js['table_id']
        s = tbl_str[id]
        qst = js['question']
        nl = s + '\nQ: ' + qst + '\nA: '
        q_s.append(nl)

        sql = js['sql']
        a = fix_repr(sql,tbl_cols[id],tbl_types[id],id)
        a = a + "\nEND\n"
        a_s.append(a)

M = len(q_s)

data_txt = [q_s[i] + a_s[i] for i in range(M)]

for i in range(5):
    j = random.randint(0,M-1)
    print()
    print(data_txt[j]) 
        
   


table: 1-20246201-9
columns: Candidate,Office,Home state,Popular vote,States – first place,States – second place,States – third place
Q: How many states-first place are there for the office of Governor?
A: SELECT COUNT States – first place FROM 1-20246201-9 WHERE Office = 'Governor'
END


table: 2-17429402-7
columns: School,Years of Participation,OCC Championships,Last OCC Championship,Last Outright OCC Championship
Q: How many times have Central Crossing won the OCC Championship?
A: SELECT SUM OCC Championships FROM 2-17429402-7 WHERE School = 'central crossing'
END


table: 1-11677691-10
columns: Player,Position,School,Hometown,College
Q: What town is Muscle Shoals High School located in?
A: SELECT  Hometown FROM 1-11677691-10 WHERE School = 'Muscle Shoals High School'
END


table: 2-10701914-2
columns: Home team,Home team score,Away team,Away team score,Venue,Crowd,Date
Q: What is the largest crowd when st kilda was the away team?
A: SELECT MAX Crowd FROM 2-10701914-2 WHERE Away te

In [5]:
toks = [tokenizer(s) for s in data_txt]


In [6]:
import numpy as np
import pandas as pd

print(len(toks[0].input_ids))
lens = np.array([len(tok.input_ids) for tok in toks])
print(pd.DataFrame(lens).describe())

z = zip(q_s,lens)
q_red = [a for a,b in z if b < 100]
z = zip(a_s,lens)
a_red = [a for a,b in z if b < 100]

data_red = [q_red[i] + a_red[i] for i in range(len(q_red))]
print(len(data_red))



92
                  0
count  56355.000000
mean     101.219519
std       21.740325
min       63.000000
25%       87.500000
50%       97.000000
75%      109.000000
max      461.000000
32084


In [7]:
import random, datasets
#d = {'prompt': random.sample(data_red, 1000)}
d = {'prompt': data_red}

data = datasets.Dataset.from_dict(d)
data = data.map(lambda x:
        tokenizer(
        x['prompt'],
        truncation=True,
        max_length=100,
        padding="max_length"
        ))

data = data.remove_columns('prompt')


Map:   0%|          | 0/32084 [00:00<?, ? examples/s]

In [8]:
#from peft import get_peft_model,PrefixTuningConfig, TaskType, PeftType
from peft import get_peft_config, get_peft_model, PromptTuningInit, PromptTuningConfig, TaskType, PeftType
import torch
import transformers
import datasets

BATCH = 128
MICRO_BATCH = 4
N_GAS = BATCH//MICRO_BATCH
EPOCHS = 1
LR = 1e-6

#peft_cfg = PrefixTuningConfig(task_type=TaskType.CAUSAL_LM, num_virtual_tokens=30)
#model = get_peft_model(model,peft_config)
#model = model.to(torch.device('cuda'))

targs = transformers.TrainingArguments(
    per_device_train_batch_size=MICRO_BATCH,
    gradient_accumulation_steps=N_GAS,
    warmup_steps=20,
    num_train_epochs=EPOCHS,
    learning_rate=LR,
    fp16=True,
    logging_steps=1,
    output_dir='sqllama-out3-rt',
    save_total_limit=3,
    remove_unused_columns=False,
    
)


In [9]:
trainer = transformers.Trainer(
    model = model,
    train_dataset = data,
    args = targs,
    #data_collator=transformers.DefaultDataCollator
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False)
)
trainer.train(resume_from_checkpoint=False)
model.save_pretrained('sqllama-out3')

In [11]:
def get_query(q):
    
    toks = tokenizer(q , return_tensors='pt')
    ctoks = toks.input_ids.to('cuda')
    gen = model.generate(ctoks, max_length=100)
    return tokenizer.decode(gen[0])

M = len(q_red)

for _ in range(10):
    j = random.randint(0,M-1)
    qs = q_red[j]
    a = a_red[j]

    ma = get_query(qs)

    #print(qs)
    print('from model')
    print(ma)
    print()
    print('expected answer')
    print(a)


from model
<unk>table: 2-10806592-14
columns: Home team,Home team score,Away team,Away team score,Venue,Crowd,Date
Q: What was the away score when the home team was Melbourne?
A:  SELECT  Home team,Home team score,Away team,Away team score,Venue,Crowd,Date
FROM 2-1080

expected answer
SELECT  Away team score FROM 2-10806592-14 WHERE Home team = 'melbourne'
END

from model
<unk>table: 2-17978030-6
columns: Date,Time,Score,Set 1,Set 2,Set 3,Total
Q: What is the score when the set 3 is 26–28?
A:  SELECT  Score FROM 2-17978030-6 WHERE Set 3 = 26–28
END
\end{code}


expected answer
SELECT  Score FROM 2-17978030-6 WHERE Set 3 = '26–28'
END

from model
<unk>table: 2-12487101-6
columns: Position,Number,Name,Class,Injury (Status),Last Update
Q: for the position of rb what is the name?
A:  SELECT Name FROM 2-12487101-6 WHERE Position = 'rb'
END
\end{code}

Comment: I'm not sure what you mean by "the name of

expected answer
SELECT  Name FROM 2-12487101-6 WHERE Position = 'rb'
END

from model
<un